In [68]:
import string
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfpage import PDFPage
from io import StringIO

import io
import os

import nltk
from nltk import word_tokenize, sent_tokenize
from nltk.stem.snowball import SnowballStemmer
from nltk.corpus import stopwords
import numpy as np
import pandas as pd

import json
from pathlib import *

import time

from random import randint

from nltk.corpus import wordnet

import operator

from nltk.chunk import tree2conlltags
nltk.download('averaged_perceptron_tagger')
nltk.download('maxent_ne_chunker')
nltk.download('words')

import re

from pdfminer.high_level import extract_text
from sklearn.preprocessing import LabelEncoder
from collections import defaultdict
from nltk.corpus import wordnet as wn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn import model_selection, naive_bayes, svm
from sklearn.metrics import accuracy_score


[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/himanshusaroha/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /Users/himanshusaroha/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to
[nltk_data]     /Users/himanshusaroha/nltk_data...
[nltk_data]   Package words is already up-to-date!


In [3]:
def pdfRender():
    global documentSet
    global mydoc
    mydoc ={}
    pdf_files =[]
    allLines =[]
    FILE_PATH = Path(r'Files/Document')
    #FILE_PATH = Path('E:/MasterThesis/FinalPapers')
    pdf_files = list(FILE_PATH.glob('*.pdf'))
    #An Array which stores the full text of each document
    documentSet = pdfparser(pdf_files)
    mydoc = dict(zip(pdf_files,documentSet))
    #print(len(documentSet))
    return documentSet

In [4]:
def pdfparser(pdffileS):
    global data_dict
    data_dict = {}
    for i in pdffileS:
        text = extract_text(i)
        data_dict[i] = text
        print(i,"done")
    return data_dict

In [5]:
pdfRender()

Files/Document/49.pdf done
Files/Document/61.pdf done
Files/Document/75.pdf done
Files/Document/74.pdf done
Files/Document/60.pdf done
Files/Document/48.pdf done
Files/Document/89.pdf done
Files/Document/76.pdf done
Files/Document/62.pdf done
Files/Document/63.pdf done
Files/Document/77.pdf done
Files/Document/88.pdf done
Files/Document/98.pdf done
Files/Document/73.pdf done
Files/Document/67.pdf done
Files/Document/9.pdf done
Files/Document/8.pdf done
Files/Document/66.pdf done
Files/Document/72.pdf done
Files/Document/99.pdf done
Files/Document/64.pdf done
Files/Document/70.pdf done
Files/Document/59.pdf done
Files/Document/71.pdf done
Files/Document/65.pdf done
Files/Document/16.pdf done
Files/Document/17.pdf done
Files/Document/100.pdf done
Files/Document/29.pdf done
Files/Document/15.pdf done
Files/Document/14.pdf done
Files/Document/28.pdf done
Files/Document/10.pdf done
Files/Document/38.pdf done
Files/Document/39.pdf done
Files/Document/11.pdf done
Files/Document/13.pdf done
Fi

{PosixPath('Files/Document/49.pdf'): 'Decision Support Systems 88 (2016) 51–66\n\nContents lists available at ScienceDirect\n\nDecision Support Systems\n\nj o u r n a l h o m e p a g e : w w w . e l s e v i e r . c o m / l o c a t e / d s s\n\nA multi-agent system to support evidence based medicine and clinical\ndecision making via data sharing and data privacy\nHayden Wimmer a, Victoria Y. Yoon b,⁎, Vijayan Sugumaran c\na Department of Information Technology, Georgia Southern University, P.O. Box 8150, Statesboro, GA 30460, United States\nb Department of Information Systems, Virginia Commonwealth University, 301 W. Main St., P. O. Box 844000, Richmond, VA 23284-4000, United States\nc Department of Decision and Information Sciences, School of Business Administration, Oakland University, 442 Elliott Hall, Rochester, MI 48309, United States\n\na r t i c l e\n\ni n f o\n\na b s t r a c t\n\nArticle history:\nReceived 19 September 2015\nReceived in revised form 23 May 2016\nAccepted 24 May

In [6]:
len(data_dict)

99

In [7]:
def processData(rawContents):    
    cleaned = tokenizeContent(rawContents)    
    cleaned1 = removeStopWordsFromTokenized(cleaned)    
    cleaned2 = performPorterStemmingOnContents(cleaned1)    
    cleaned3 = removePunctuationFromTokenized(cleaned2)    
    cleaned4 = convertItemsToLower(cleaned3)    
    return cleaned4    
        
def tokenizeContent(contentsRaw):    
    tokenized = nltk.tokenize.sent_tokenize(contentsRaw)    
    return tokenized    
    
def removeStopWordsFromTokenized(contentsTokenized):    
    stop_word_set = set(nltk.corpus.stopwords.words("english"))    
    filteredContents = [word for word in contentsTokenized if word not in stop_word_set]    
    return filteredContents    
    
def performPorterStemmingOnContents(contentsTokenized):    
    porterStemmer = nltk.stem.PorterStemmer()    
    filteredContents = [porterStemmer.stem(word) for word in contentsTokenized]    
    return filteredContents    
    
def removePunctuationFromTokenized(contentsTokenized):    
    excludePuncuation = set(string.punctuation)    
    
    # manually add additional punctuation to remove    
    doubleSingleQuote = '\'\''    
    doubleDash = '--'    
    doubleTick = '``'    
    
    excludePuncuation.add(doubleSingleQuote)    
    excludePuncuation.add(doubleDash)    
    excludePuncuation.add(doubleTick)    
    
    filteredContents = [word for word in contentsTokenized if word not in excludePuncuation]    
    return filteredContents    
    
def convertItemsToLower(contentsRaw):    
    filteredContents = [term.lower() for term in contentsRaw]    
    return filteredContents


In [8]:
for name,text in data_dict.items():
    data_dict[name] = processData(str(text))

In [9]:
cleanDocx = []
for i in data_dict:
    doc = str(data_dict[i])
    doc = processData(doc)
    doc = [i.replace('\\n', "") for i in doc]
    doc = [i.replace('\\x0', "") for i in doc]
    cleanDocx.append(doc)
print(len(cleanDocx))

99


In [10]:
cleanDocx[2]

["['decision support systems 50 (2011) 559–569contents lists available at sciencedirectdecision support systemsj o u r n a l h o m e p a g e : w w w. e l s ev i e r. c o m / l o c a t e / d s sthe application of data mining techniques in ﬁnancial fraud detection: a classiﬁcationframework and an academic review of literaturee.w.t.",
 "', 'ngai a, yong hu b,⁎, y.h.",
 "', 'wong a, yijun chen b, xin sun ba department of management and marketing, the hong kong polytechnic university, kowloon, hong kong, pr chinab institute of business intelligence and knowledge discovery, department of e-commerce, guangdong university of foreign studies, sun yat-sen university, guangzhou 510006, pr chinaa r t i c l ei n f oa b s t r a c tavailable online 19 august 2010keywords:financial fraudfraud detectionliterature reviewdata miningbusiness intelligencethis paper presents a review of — and classiﬁcation scheme for — the literature on the application of datamining techniques for the detection of ﬁnancial 

In [11]:
cleanedData = []
for doc in range(len(cleanDocx)):
    doc = str(cleanDocx[doc])
    cleanedData.append(doc)

In [12]:
#perform cleaning to remove all the two and three letter words
fCleanedData = []
for i in range(len(cleanedData)):
    formattedData = cleanedData[i]
    finalCleanData = re.sub(r'\b\w{1,3}\b', '', formattedData)
    fCleanedData.append(finalCleanData)

In [13]:
len(fCleanedData)

99

In [14]:
%store fCleanedData

Stored 'fCleanedData' (list)


In [15]:
dfObj = pd.DataFrame(fCleanedData) 

In [16]:
dfObj1 = dfObj.dropna(axis=1)

In [27]:
dfObj1[0] = dfObj1[0].str.strip('\'')
                             

dfObj1.head()
dfObj1.rename(columns={0:"text"},inplace=True)

In [130]:
label = []
review = ['systematic literature review', 'literature review', 'systematic review']
analysis = ['data mining','natural language processing', 'text Mining', 'text classification', 'text analysis']
aim = ["aim" , "objective" ,"motivation" , "objectives" , "goal"]
methods= ["methods" , "methodology" ,"research methodology" , "approach", "techniques"]
conclusion = ["conclusions" , "discussions" , "justifications" , "summary" ,"finally" , "result"]
words_list={"review":review,"analysis":analysis,"aim":aim,"methods":methods,"conclusion":conclusion}
for i in fCleanedData:
    removed = []
    found = []
    for j in i.split():
        for k in words_list:
            if j.lower() in words_list[k] and j.lower() not in removed:
                removed.append(j.lower())
                if k not in found:
                    found.append(k)
    if len(found)>4:
        label.append("most relevent")
    elif len(found)>2:
        label.append("relevent")
    else:
        label.append("rejected")

In [131]:
dfObj1["label"] = label

In [133]:
sum(dfObj1.label=="relevent")

77

In [134]:
np.random.seed(200)

In [135]:
from sklearn.model_selection import train_test_split

In [136]:
X = dfObj1["text"]
y = dfObj1["label"]

In [137]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

In [138]:
Encoder = LabelEncoder()
y_train = Encoder.fit_transform(y_train)
y_test = Encoder.fit_transform(y_test)

In [139]:
Tfidf_vect = TfidfVectorizer(max_features=5000)
Tfidf_vect.fit(dfObj1['text'])
Train_X_Tfidf = Tfidf_vect.transform(X_train)
Test_X_Tfidf = Tfidf_vect.transform(X_test)

In [140]:
print(Tfidf_vect.vocabulary_)

{'decision': 1216, 'support': 4369, 'systems': 4414, '2016': 73, 'lists': 2658, 'available': 480, 'multi': 2978, 'agent': 241, 'system': 4407, 'evidence': 1668, 'based': 504, 'medicine': 2837, 'making': 2732, 'data': 1187, 'sharing': 4075, 'yoon': 4963, 'department': 1253, 'information': 2330, 'technology': 4458, 'university': 4712, 'united': 4707, 'main': 2718, 'sciences': 3973, 'school': 3969, 'business': 645, 'administration': 210, 'hall': 2084, 'history': 2153, 'received': 3685, 'september': 4046, 'revised': 3876, 'form': 1891, 'online': 3135, 'june': 2503, 'preserving': 3462, 'modern': 2929, 'standard': 4244, 'clinical': 849, 'where': 4883, 'medical': 2834, 'with': 4909, 'expertise': 1722, 'research': 3817, 'decisions': 1217, 'supporting': 4371, 'requires': 3815, 'access': 140, 'accurate': 159, 'predictive': 3440, 'models': 2927, 'dimensional': 1349, 'patient': 3279, 'view': 4814, 'that': 4493, 'aggregated': 245, 'from': 1941, 'multiple': 2985, 'sources': 4190, 'healthcare': 2112,

In [141]:
print(Train_X_Tfidf)

  (0, 4999)	0.006853192198465426
  (0, 4997)	0.011590759932013797
  (0, 4996)	0.0038798657151981417
  (0, 4992)	0.00358813007625974
  (0, 4985)	0.0029875864661538577
  (0, 4984)	0.002348779138062959
  (0, 4983)	0.0772474677628834
  (0, 4977)	0.007336822295273166
  (0, 4976)	0.03289783774797475
  (0, 4971)	0.00717626015251948
  (0, 4965)	0.0061952714850444885
  (0, 4956)	0.0015258828866206973
  (0, 4955)	0.001590415939503353
  (0, 4953)	0.026755664215327962
  (0, 4949)	0.007009337712803155
  (0, 4929)	0.011986521244070325
  (0, 4925)	0.009448537773736857
  (0, 4920)	0.002674326637855538
  (0, 4912)	0.001641180361561629
  (0, 4911)	0.0014063083021908873
  (0, 4910)	0.016490474541976143
  (0, 4909)	0.15639882803031518
  (0, 4908)	0.00717626015251948
  (0, 4895)	0.003575983091646469
  (0, 4894)	0.0020482134754409623
  :	:
  (65, 281)	0.01076319853245197
  (65, 276)	0.01010845372759945
  (65, 268)	0.01420749717737341
  (65, 266)	0.014062526993532864
  (65, 262)	0.019497931205135523
  (65, 2

In [142]:
SVM = svm.SVC(C=1.0, kernel='linear', degree=3, gamma='auto')
SVM.fit(Train_X_Tfidf,y_train)
# predict the labels on validation dataset
predictions_SVM = SVM.predict(Test_X_Tfidf)
# Use accuracy_score function to get the accuracy
print("SVM Accuracy Score -> ",accuracy_score(predictions_SVM, y_test)*100)

SVM Accuracy Score ->  72.72727272727273


In [143]:
%store dfObj1

Stored 'dfObj1' (DataFrame)


In [144]:
%store X_train

Stored 'X_train' (Series)


In [145]:
%store y_train
%store X_test
%store y_test
%store Train_X_Tfidf
%store Test_X_Tfidf

Stored 'y_train' (ndarray)
Stored 'X_test' (Series)
Stored 'y_test' (ndarray)
Stored 'Train_X_Tfidf' (csr_matrix)
Stored 'Test_X_Tfidf' (csr_matrix)
